### This notebook uses a breathing actuation sequence that computes triggers inflation deflation based upon an average inhale/exhale duration and a scale factor

In [1]:
from pythonosc import dispatcher, osc_server
from pythonosc.udp_client import SimpleUDPClient
import biofeatures
import threading
import numpy as np
import time
from random import uniform

In [2]:
def data_handler(unused_addr, args, data1, data2, data3, data4, data5, data6): #BITalino ServerBIT format
    global ecg_data, resp_data
    global osc_client
        
    B = args[0]
    HR = args[1]
    
    # BITalino ServerBIT
    ecg_data.append(float(np.random.rand(1)))
    resp_data.append(float(data6))
        
    if B.is_warmed_up:
        B.set_data(resp_data[-B.buffer_length:])
    
    if HR.is_warmed_up:
        HR.set_data(ecg_data[-HR.buffer_length:])


In [3]:
def riot_data_handler(unused_addr, args, *values): #R-IoT 
    global ecg_data, resp_data
    global osc_client
    
    B = args[0]
    HR = args[1]
    
#     ecg_data.append(float(values[13]))
    ecg_data.append(np.random.rand(1)[0])
    resp_data.append(float(values[12])) 
        
    if B.is_warmed_up:
        B.set_data(resp_data[-B.buffer_length:])
    
    if HR.is_warmed_up:
        HR.set_data(ecg_data[-HR.buffer_length:])
    


In [4]:
def warmup(B, resp_data, HR, ecg_data):
    """Function to launch once the system has warmed up.
    Sets the  data initially and launches a recursive update of features.
    Parameters
    ----------
    B: object containing breathing data and features
    resp_data: respiration signal data to set
    HR: object containing ECG data and features
    ecg_data: ecg signal data to set
    """
    
    if not B.is_warmed_up:
        print("Breathing WARMUP")
        B.set_data(resp_data[-B.buffer_length:])
        B.is_warmed_up = True
        B.update_loop()
        
    if not HR.is_warmed_up:
        print("ECG WARMUP")
        HR.set_data(ecg_data[-HR.buffer_length:])
        HR.is_warmed_up = True
        HR.update_loop()
        
#         act_launcher(B, resp_data, HR, ecg_data) # No thread based

        timer_act = threading.Timer(0.1, act_launcher, [B, resp_data, HR, ecg_data] ) # Thread based
        timer_act.start() # Thread based
        
#     breathing_factor = B.breathing_factor
    
#     if B.routine == "None":
#         print("n-----")

#     elif B.routine == "breathing_biofeedback":
#         timer_actuation1 = threading.Timer(0.1, breathing_biofeedback, ["1", B, True] )
#         timer_actuation1.start()
    
#         timer_actuation2 = threading.Timer(0.1, breathing_biofeedback, ["2", B, True] )
#         #timer_actuation2 = threading.Timer(0.1, pulsating, ["2", True] )
#         timer_actuation2.start()

#     elif B.routine == "pulsating":
#         pass

In [5]:
def act_launcher(B, resp_data, HR, ecg_data):
    global actuation_flag
    global act_one, act_two
    
    if B.routine == "None":
        print("n-------")

    elif B.routine == "breathing_biofeedback":
        breathing_factor = B.breathing_factor
        if act_one:
            timer_actuation1 = threading.Timer(0.1, breathing_biofeedback, ["1", B, True] )
            timer_actuation1.start()
        
        if act_two:
            timer_actuation2 = threading.Timer(0.1, breathing_biofeedback, ["2", B, True] )
            #timer_actuation2 = threading.Timer(0.1, pulsating, ["2", True] )
            timer_actuation2.start()

    elif B.routine == "pulsating":
        if act_one:
            timer_actuation1 = threading.Timer(0.1, pulsating, ["1", True] )
            timer_actuation1.start()

        if act_two:
            timer_actuation2 = threading.Timer(0.1, pulsating, ["2", True] )
            timer_actuation2.start()        

    elif B.routine == "random_inflation":
        if act_one:
            timer_actuation1 = threading.Timer(0.1, random_inflation , ["1", 2, 5, True] )
            timer_actuation1.start()
            
        if act_two:
            timer_actuation2 = threading.Timer(0.1, random_inflation, ["1", 2, 5, True] )
            timer_actuation2.start()        
    
    elif B.routine == "async_intervals":
        timer_actuation = threading.Timer(0.1, async_intervals, ["1", "2", 3, 3, True] )
        timer_actuation.start()

    elif B.routine == "async_breathing":
        timer_actuation = threading.Timer(0.1, async_breathing, ["1", "2", B, True] )
        timer_actuation.start()    
    
    elif B.routine.startswith("Deflate"):
        def_duration = int(B.routine[7:])
        
        if act_one:
            timer_actuation1 = threading.Timer(0.1, deflate, ["1", def_duration] )
            timer_actuation1.start()
        
        if act_two:
            timer_actuation1 = threading.Timer(0.1, deflate, ["2", def_duration] )
            timer_actuation1.start()
        
    elif B.routine.startswith("Inflate"):
        inf_duration = int(B.routine[7:])
        
        if act_one:
            timer_actuation1 = threading.Timer(0.1, warmup_inflate, ["1", inf_duration] )
            timer_actuation1.start()
        
        if act_two:
            timer_actuation1 = threading.Timer(0.1, warmup_inflate, ["2", inf_duration] )
            timer_actuation1.start()
        
    elif B.routine.startswith("Offset"):
        values = list(map(lambda x: int(x), B.routine.split(",")[1:]))
        offset_intervals("1", "2", values[0], values[1], values[2], B)

In [6]:
def warmup_inflate(act_id, duration):
    global osc_client
    
    print(duration)
    osc_client.send_message("/actuator/" + act_id + "/inflate", 100.0)
    time.sleep(duration)
    osc_client.send_message("/actuator/" + act_id + "/inflate", 0.0)


In [7]:
def deflate(act_id, duration):
    global osc_client
    
    osc_client.send_message("/actuator/" + act_id + "/inflate", -100.0)
    time.sleep(duration)
    osc_client.send_message("/actuator/" + act_id + "/inflate", 0.0)


### Different actuation sequences

In [8]:
# computes inhale and exhale interval duration as average duration of breath * breathing_factor 
def breathing_biofeedback(act_id, B, inflate):
    global osc_client 
    global actuation_flag
    global act_one, act_two
    
    if (act_id == "1" and not act_one) or (act_id == "2" and not act_two):
        osc_client.send_message("/actuator/" + act_id + "/inflate", 0.0)
        return
    
    if not actuation_flag or B.routine != "breathing_biofeedback":
        return


#     if not actuation_flag:
#         return
    
    breathing_factor = B.breathing_factor
#     print("BrF: ", breathing_factor)  
    
    if inflate:
        #print("inhale: ", B.features['avg_inhale'])
        osc_client.send_message("/actuator/" + act_id + "/inflate", 100.0)
        timer_exhale = threading.Timer(B.features['avg_inhale'] * breathing_factor, breathing_biofeedback, [act_id, B, False])
        timer_exhale.start()
        
        for i in range(1,10):
            osc_client.send_message("/actuator/" + act_id + "/inflate", 100.0)

    else:
        #print("exhale: ", B.features['avg_inhale'])
        osc_client.send_message("/actuator/" + act_id + "/inflate", -100.0)
        timer_inhale = threading.Timer(B.features['avg_inhale'] * breathing_factor, breathing_biofeedback, [act_id, B, True])
        timer_inhale.start()
        
        for i in range(1,10):
            osc_client.send_message("/actuator/" + act_id + "/inflate", -100.0)


In [9]:
# specify inhale and exhale interval duration in seconds
def intervals(act_id, inhale_duration, exhale_duration, inflate):
    global osc_client, actuation_flag
    global act_one, act_two
    
    if (act_id == "1" and not act_one) or (act_id == "2" and not act_two):
        osc_client.send_message("/actuator/" + act_id + "/inflate", 0.0)
        return
    
    if not actuation_flag or not B.routine.startswith("Offset"):
        return
    
    if inflate:
        print("inhale: ", inhale_duration)
        osc_client.send_message("/actuator/" + act_id + "/inflate", 100.0)
        timer_exhale = threading.Timer(inhale_duration, intervals, [act_id, inhale_duration, exhale_duration, False])
        timer_exhale.start()

    else:
        print("exhale: ", exhale_duration)
        osc_client.send_message("/actuator/" + act_id + "/inflate", -100.0)
        timer_inhale = threading.Timer(exhale_duration, intervals, [act_id, inhale_duration, exhale_duration, True])
        timer_inhale.start()

In [10]:
def pulsating(act_id,inflate):
    global osc_client
    global actuation_flag
    global act_one, act_two
    
    if (act_id == "1" and not act_one) or (act_id == "2" and not act_two):
        osc_client.send_message("/actuator/" + act_id + "/inflate", 0.0)
        return
    
    if not actuation_flag or B.routine != "pulsating":
        return
    
    if inflate:
        osc_client.send_message("/actuator/" + act_id + "/inflate", 50.0)
        timer_deflate = threading.Timer(3, pulsating, [act_id, False])
        timer_deflate.start()

    else:
        osc_client.send_message("/actuator/" + act_id + "/inflate", -50.0)
        timer_inflate = threading.Timer(3, pulsating, [act_id, True])
        timer_inflate.start()

In [11]:
def random_inflation(act_id, lower, upper, inflate):
    global osc_client, actuation_flag
    global act_one, act_two
    
    if (act_id == "1" and not act_one) or (act_id == "2" and not act_two):
        osc_client.send_message("/actuator/" + act_id + "/inflate", 0.0)
        return
    
    if not actuation_flag or B.routine != "random_inflation":        
        return
    
    int_length = uniform(lower,upper)
    
    if inflate:
        osc_client.send_message("/actuator/" + act_id + "/inflate", 100.0)
        timer_deflate = threading.Timer(int_length, random_inflation, [act_id, lower, upper, False])
        timer_deflate.start()

    else:
        osc_client.send_message("/actuator/" + act_id + "/inflate", -100.0)
        timer_inflate = threading.Timer(int_length, random_inflation, [act_id, lower, upper, True])
        timer_inflate.start()

In [12]:
def async_intervals(act_first, act_snd, inhale_dur, exhale_dur, inflate_first):
    global osc_client, actuation_flag
    
    if not actuation_flag or B.routine != "async_intervals":
        return
    
    if inflate_first:
        print("inhale: ", inhale_dur)
        osc_client.send_message("/actuator/" + act_first + "/inflate", 100.0)
        osc_client.send_message("/actuator/" + act_snd + "/inflate", -100.0)
        timer_inhale = threading.Timer(inhale_dur, async_intervals, [act_first, act_snd, inhale_dur, exhale_dur, False])
        timer_inhale.start()

    else:
        print("exhale: ", exhale_dur)
        osc_client.send_message("/actuator/" + act_first + "/inflate", -100.0)
        osc_client.send_message("/actuator/" + act_snd + "/inflate", 100.0)
        timer_exhale = threading.Timer(exhale_dur, async_intervals, [act_first, act_snd, inhale_dur, exhale_dur, True])
        timer_exhale.start()

In [13]:
def async_breathing(act_first, act_snd, B, inflate):
    global osc_client, actuation_flag
    
    if not actuation_flag or B.routine != "async_breathing":
        return

    breathing_factor = B.breathing_factor
    
    if inflate:
        print("inhale: ", B.features['avg_inhale'])
        osc_client.send_message("/actuator/" + act_first + "/inflate", 100.0)
        osc_client.send_message("/actuator/" + act_snd + "/inflate", -100.0)
        timer_exhale = threading.Timer(B.features['avg_inhale'] * breathing_factor, async_breathing, [act_first, act_snd, B, False])
        timer_exhale.start()

    else:
        print("exhale: ", B.features['avg_exhale'])
        osc_client.send_message("/actuator/" + act_first + "/inflate", -100.0)
        osc_client.send_message("/actuator/" + act_snd + "/inflate", 100.0)
        timer_inhale = threading.Timer(B.features['avg_exhale'] * breathing_factor, async_breathing, [act_first, act_snd, B, True])
        timer_inhale.start()

In [14]:
def offset_intervals(act_first, act_second, int_first, int_snd, offset, B):
    global actuation_flag
    
    if not actuation_flag or not B.routine.startswith("Offset"):
        return
    
    intervals(act_first, int_first, int_first, True);
    
    timer_snd = threading.Timer(offset, intervals, [act_second, int_snd, int_snd, True])
    timer_snd.start()


In [15]:
# computes degree of inflation/deflation based on ECG features

# TODO: how to compute the inflation/deflation value?

def heartrate_actuation(act_id, HR, timer_interval):
    global osc_client, actuation_flag
    global act_one, act_two
    
    if (act_id == "1" and not act_one) or (act_id == "2" and not act_two):
        osc_client.send_message("/actuator/" + act_id + "/inflate", 0.0)
        return
    
    if not actuation_flag:
        return
    
    current_trend = HR.current_trends["hr_mean"]
    #current_trend = HR.current_trends["rmssd"]
    #current_trend = HR.current_trends["LF/HF ratio"]
    
    current_feature = HR.features[-1]["hr_mean"]
    #current_feature = HR.features[-1]["rmssd"]
    #current_feature = HR.features[-1]["LF/HF ratio"]
    
    if current_trend > 0:
        osc_client.send_message("/actuator/" + act_id + "/inflate", 100.0)
        #osc_client.send_message("/actuator/" + act_id + "/inflate", current_trend * 1000/current_feature)
        timer_exhale = threading.Timer(timer_interval, heartrate_actuation, [act_id, HR, timer_interval])
        timer_exhale.start()

    else:
        #osc_client.send_message("/actuator/inflate", current_trend * 1000/current_feature)
        osc_client.send_message("/actuator/" + act_id + "/inflate", -100.0)
        timer_inhale = threading.Timer(timer_interval, heartrate_actuation, [act_id, HR, timer_interval])
        timer_inhale.start()

#### Set up configuration: IP (BITalino, R-IoT or Node-RED), port and OSC address pattern

In [16]:
def hold_down():
    global actuation_flag
    a = 0
    return

In [17]:
def conf_handler(unused_addr, args, *values): #Conf 

    global ecg_data, resp_data
    global actuation_flag
    global osc_client
    global act_one, act_two
    
    B = args[0]
    HR = args[1]   

    print("----------------- ACTUATION CHANGE ------------------------")
    print(values)
    
    if type(values[0]) == str and values[0].startswith("act"):
        if values[0] == "act1":
            if act_two:
                osc_client.send_message("/actuator/2/inflate", 0)
            act_one = True
            act_two = False
        elif values[0] == "act2":
            if act_one:
                osc_client.send_message("/actuator/1/inflate", 0)
            act_one = False
            act_two = True
        elif values[0] == "act12":
            act_one = True
            act_two = True
        
        timer_act = threading.Timer(0.1, act_launcher, [B, resp_data, HR, ecg_data] )
        #timer_act.start()
        
    elif type(values[0]) == str:
        if B.routine != values[0]:
            B.routine = values[0]

        if B.routine == "stop_all":
            actuation_flag = False
            val = 0.0
            osc_client.send_message("/actuator/1/inflate", val)
            osc_client.send_message("/actuator/2/inflate", val)
        
        if B.routine == "None":
            if act_one:
                act_one = False
                osc_client.send_message("/actuator/1/inflate", 0)
            if act_two:
                act_two = False
                osc_client.send_message("/actuator/2/inflate", 0)

        else:
            actuation_flag = True
                
            print(B.routine)
            timer_act = threading.Timer(3, act_launcher, [B, resp_data, HR, ecg_data] )
            timer_act.start()
        
    elif type(values[0]) == float: 
        B.breathing_factor = np.round(values[0],1)
        print("BrF val:", B.breathing_factor)
    
    else:
        print("NodeRED value: ", values[0])

In [20]:
# Definitions
bitalino_ip = '192.168.0.100'
bitalino_port = 8000
bitalino_srate = 100

riot_ip = "192.168.0.100"
riot_port = 31000 
riot_srate = 200

# riot_ip = "192.168.1.40"
# riot_port = 12000 

#actuator_ip = '192.168.0.110'
actuator_ip = '192.168.0.100'
actuator_port = 32000

riot_address = "/0/raw" 
bitalino_address = "/0/bitalino"


###### CONFIGURATION 
config_address = riot_address
config_ip = riot_ip
config_port = riot_port
srate = riot_srate 
C = {"config_address": config_address, "config_ip": config_ip, "config_port": config_port, "srate": srate}

osc_client = SimpleUDPClient(actuator_ip, actuator_port) 

actuation_flag = True

ecg_data = []
resp_data = []

act_one = True
act_two = True

B = biofeatures.breathing(data = np.ones(10), buffer_length=2000, srate=srate)
HRV = biofeatures.hrv(data = np.ones(10), buffer_length=2000, srate=srate)
B.breathing_factor = 1.0
B.routine = "breathing_biofeedback" 


my_dispatcher = dispatcher.Dispatcher()
my_dispatcher.map(config_address, riot_data_handler, B, HRV)
my_dispatcher.map("/brf/", conf_handler, B, HRV)


server = osc_server.ThreadingOSCUDPServer((config_ip, config_port), my_dispatcher)
print (C)
print("Serving on {}".format(server.server_address))

# Warmup
warmup_t = 10
timer_warmup = threading.Timer(warmup_t, warmup, [B,resp_data,HRV,ecg_data])
timer_warmup.start()

try: 
    server.serve_forever()
except KeyboardInterrupt:
    B.update_data_flag = False
    HRV.update_data_flag = False
    actuation_flag = False
    server.server_close()
    osc_client.send_message("/actuator/1/inflate", 0.0)
    osc_client.send_message("/actuator/2/inflate", 0.0)
except:
    raise

{'config_address': '/0/raw', 'config_ip': '192.168.0.100', 'config_port': 31000, 'srate': 200}
Serving on ('192.168.0.100', 31000)
Breathing WARMUP
{'breath_avg_len': 3.33, 'inhale_duration': 4.72, 'avg_inhale': 2.36, 'exhale_duration': 5.27, 'avg_exhale': 1.76, 'inhale_exhale_ratio': 0.9}
ECG WARMUP
[{'nni_mean': 444.47, 'hr_mean': 164.13, 'hr_std': 65.52, 'rmssd': 310.13, 'lf': 5089.15, 'hf': 13755.59, 'LF/HF ratio': 0.37}]
{'breath_avg_len': 3.33, 'inhale_duration': 4.87, 'avg_inhale': 2.44, 'exhale_duration': 5.12, 'avg_exhale': 1.71, 'inhale_exhale_ratio': 0.95}
[{'nni_mean': 444.47, 'hr_mean': 164.13, 'hr_std': 65.52, 'rmssd': 310.13, 'lf': 5089.15, 'hf': 13755.59, 'LF/HF ratio': 0.37}, {'nni_mean': 363.65, 'hr_mean': 180.24, 'hr_std': 50.42, 'rmssd': 164.82, 'lf': 2087.9, 'hf': 2029.62, 'LF/HF ratio': 1.03}]
----------------- ACTUATION CHANGE ------------------------
('stop_all',)
stop_all
{'breath_avg_len': 2.5, 'inhale_duration': 5.6, 'avg_inhale': 1.87, 'exhale_duration': 4.3

{'breath_avg_len': 3.33, 'inhale_duration': 5.08, 'avg_inhale': 1.69, 'exhale_duration': 4.91, 'avg_exhale': 2.46, 'inhale_exhale_ratio': 1.03}
[{'nni_mean': 354.81, 'hr_mean': 185.94, 'hr_std': 54.32, 'rmssd': 174.64, 'lf': 519.17, 'hf': 2442.33, 'LF/HF ratio': 0.21}, {'nni_mean': -24.22, 'hr_mean': 181.3, 'hr_std': 66.17, 'rmssd': 1986.12, 'lf': 55845.18, 'hf': 9188.97, 'LF/HF ratio': 6.08}, {'nni_mean': 486.84, 'hr_mean': 147.98, 'hr_std': 60.58, 'rmssd': 386.22, 'lf': 819.5, 'hf': 23680.34, 'LF/HF ratio': 0.03}, {'nni_mean': -54.16, 'hr_mean': 142.3, 'hr_std': 69.55, 'rmssd': 2433.51, 'lf': 111569.63, 'hf': 33260.86, 'LF/HF ratio': 3.35}, {'nni_mean': -15.16, 'hr_mean': 164.0, 'hr_std': 63.8, 'rmssd': 2077.68, 'lf': 66880.79, 'hf': 9948.94, 'LF/HF ratio': 6.72}]
{'breath_avg_len': 3.33, 'inhale_duration': 4.92, 'avg_inhale': 1.64, 'exhale_duration': 5.07, 'avg_exhale': 2.54, 'inhale_exhale_ratio': 0.97}
[{'nni_mean': -24.22, 'hr_mean': 181.3, 'hr_std': 66.17, 'rmssd': 1986.12, 'lf'

{'breath_avg_len': 5.0, 'inhale_duration': 5.22, 'avg_inhale': 2.61, 'exhale_duration': 4.76, 'avg_exhale': 2.38, 'inhale_exhale_ratio': 1.1}
[{'nni_mean': 400.0, 'hr_mean': 166.37, 'hr_std': 55.82, 'rmssd': 203.33, 'lf': 52.7, 'hf': 2126.1, 'LF/HF ratio': 0.02}, {'nni_mean': -10.58, 'hr_mean': 158.72, 'hr_std': 66.85, 'rmssd': 2098.84, 'lf': 57213.77, 'hf': 11067.79, 'LF/HF ratio': 5.17}, {'nni_mean': 407.83, 'hr_mean': 165.26, 'hr_std': 58.53, 'rmssd': 215.94, 'lf': 47.0, 'hf': 868.62, 'LF/HF ratio': 0.05}, {'nni_mean': -60.43, 'hr_mean': 150.18, 'hr_std': 63.34, 'rmssd': 2372.03, 'lf': 132754.54, 'hf': 15819.31, 'LF/HF ratio': 8.39}, {'nni_mean': -19.96, 'hr_mean': 154.21, 'hr_std': 61.03, 'rmssd': 2114.57, 'lf': 68839.93, 'hf': 9465.68, 'LF/HF ratio': 7.27}]
{'breath_avg_len': 5.0, 'inhale_duration': 5.02, 'avg_inhale': 2.51, 'exhale_duration': 4.97, 'avg_exhale': 2.48, 'inhale_exhale_ratio': 1.01}
[{'nni_mean': -10.58, 'hr_mean': 158.72, 'hr_std': 66.85, 'rmssd': 2098.84, 'lf': 57

{'breath_avg_len': 3.33, 'inhale_duration': 5.58, 'avg_inhale': 2.79, 'exhale_duration': 4.42, 'avg_exhale': 2.21, 'inhale_exhale_ratio': 1.26}
[{'nni_mean': 393.54, 'hr_mean': 168.32, 'hr_std': 55.47, 'rmssd': 152.78, 'lf': 930.75, 'hf': 6954.67, 'LF/HF ratio': 0.13}, {'nni_mean': 393.48, 'hr_mean': 169.26, 'hr_std': 56.72, 'rmssd': 166.72, 'lf': 1315.04, 'hf': 6960.2, 'LF/HF ratio': 0.19}, {'nni_mean': -20.17, 'hr_mean': 162.27, 'hr_std': 65.91, 'rmssd': 2089.33, 'lf': 75891.35, 'hf': 13608.89, 'LF/HF ratio': 5.58}, {'nni_mean': 375.4, 'hr_mean': 177.16, 'hr_std': 56.34, 'rmssd': 159.59, 'lf': 1318.4, 'hf': 5405.94, 'LF/HF ratio': 0.24}, {'nni_mean': 379.58, 'hr_mean': 175.09, 'hr_std': 55.86, 'rmssd': 155.84, 'lf': 918.77, 'hf': 4357.49, 'LF/HF ratio': 0.21}]
{'breath_avg_len': 3.33, 'inhale_duration': 5.38, 'avg_inhale': 2.69, 'exhale_duration': 4.61, 'avg_exhale': 2.31, 'inhale_exhale_ratio': 1.17}
[{'nni_mean': 393.48, 'hr_mean': 169.26, 'hr_std': 56.72, 'rmssd': 166.72, 'lf': 13

{'breath_avg_len': 3.33, 'inhale_duration': 4.49, 'avg_inhale': 1.5, 'exhale_duration': 5.5, 'avg_exhale': 1.83, 'inhale_exhale_ratio': 0.81}
[{'nni_mean': 350.58, 'hr_mean': 185.61, 'hr_std': 52.75, 'rmssd': 145.88, 'lf': 84.37, 'hf': 995.2, 'LF/HF ratio': 0.08}, {'nni_mean': 357.0, 'hr_mean': 183.03, 'hr_std': 54.22, 'rmssd': 147.14, 'lf': 37.67, 'hf': 790.88, 'LF/HF ratio': 0.05}, {'nni_mean': -28.62, 'hr_mean': 175.85, 'hr_std': 64.72, 'rmssd': 1988.47, 'lf': 46526.24, 'hf': 5888.16, 'LF/HF ratio': 7.9}, {'nni_mean': 374.38, 'hr_mean': 177.68, 'hr_std': 57.54, 'rmssd': 141.37, 'lf': 409.21, 'hf': 821.22, 'LF/HF ratio': 0.5}, {'nni_mean': 362.4, 'hr_mean': 182.16, 'hr_std': 55.47, 'rmssd': 162.72, 'lf': 361.34, 'hf': 1442.98, 'LF/HF ratio': 0.25}]
{'breath_avg_len': 3.33, 'inhale_duration': 4.02, 'avg_inhale': 1.34, 'exhale_duration': 5.97, 'avg_exhale': 1.99, 'inhale_exhale_ratio': 0.67}
[{'nni_mean': 357.0, 'hr_mean': 183.03, 'hr_std': 54.22, 'rmssd': 147.14, 'lf': 37.67, 'hf': 79

...

[{'nni_mean': -20.58, 'hr_mean': 165.16, 'hr_std': 73.72, 'rmssd': 2140.54, 'lf': 91497.88, 'hf': 10519.59, 'LF/HF ratio': 8.7}, {'nni_mean': 411.52, 'hr_mean': 174.68, 'hr_std': 70.24, 'rmssd': 282.24, 'lf': 9233.28, 'hf': 15043.59, 'LF/HF ratio': 0.61}, {'nni_mean': 443.81, 'hr_mean': 161.27, 'hr_std': 67.68, 'rmssd': 296.62, 'lf': 5175.67, 'hf': 7711.5, 'LF/HF ratio': 0.67}, {'nni_mean': 428.86, 'hr_mean': 164.86, 'hr_std': 64.62, 'rmssd': 287.09, 'lf': 4848.08, 'hf': 6304.71, 'LF/HF ratio': 0.77}, {'nni_mean': 425.91, 'hr_mean': 166.05, 'hr_std': 64.43, 'rmssd': 284.82, 'lf': 4365.33, 'hf': 5545.12, 'LF/HF ratio': 0.79}]
RESP ERROR


Exception in thread Thread-1218045:
Traceback (most recent call last):
  File "/Users/annkatrin/opt/anaconda3/lib/python3.7/threading.py", line 926, in _bootstrap_inner
    self.run()
  File "/Users/annkatrin/opt/anaconda3/lib/python3.7/threading.py", line 1178, in run
    self.function(*self.args, **self.kwargs)
  File "/Users/annkatrin/Documents/Uni/Master/KTH/Master Project/biofeatures/notebooks/biofeatures.py", line 58, in update_loop
    self.resp_intervals(data)
  File "/Users/annkatrin/Documents/Uni/Master/KTH/Master Project/biofeatures/notebooks/biofeatures.py", line 87, in resp_intervals
    processed_data = resp.resp(signal=data, sampling_rate=self.srate, show=False)
  File "/Users/annkatrin/opt/anaconda3/lib/python3.7/site-packages/biosppy/signals/resp.py", line 91, in resp
    mirror=True)
  File "/Users/annkatrin/opt/anaconda3/lib/python3.7/site-packages/biosppy/signals/tools.py", line 609, in smoother
    (signal[0] * np.ones(size), signal, signal[-1] * np.ones(size)))
In

[{'nni_mean': 411.52, 'hr_mean': 174.68, 'hr_std': 70.24, 'rmssd': 282.24, 'lf': 9233.28, 'hf': 15043.59, 'LF/HF ratio': 0.61}, {'nni_mean': 443.81, 'hr_mean': 161.27, 'hr_std': 67.68, 'rmssd': 296.62, 'lf': 5175.67, 'hf': 7711.5, 'LF/HF ratio': 0.67}, {'nni_mean': 428.86, 'hr_mean': 164.86, 'hr_std': 64.62, 'rmssd': 287.09, 'lf': 4848.08, 'hf': 6304.71, 'LF/HF ratio': 0.77}, {'nni_mean': 425.91, 'hr_mean': 166.05, 'hr_std': 64.43, 'rmssd': 284.82, 'lf': 4365.33, 'hf': 5545.12, 'LF/HF ratio': 0.79}, {'nni_mean': -26.56, 'hr_mean': 170.62, 'hr_std': 66.97, 'rmssd': 2047.92, 'lf': 61825.74, 'hf': 16106.56, 'LF/HF ratio': 3.84}]
{'breath_avg_len': 3.33, 'inhale_duration': 3.65, 'avg_inhale': 1.22, 'exhale_duration': 6.34, 'avg_exhale': 3.17, 'inhale_exhale_ratio': 0.58}
[{'nni_mean': 443.81, 'hr_mean': 161.27, 'hr_std': 67.68, 'rmssd': 296.62, 'lf': 5175.67, 'hf': 7711.5, 'LF/HF ratio': 0.67}, {'nni_mean': 428.86, 'hr_mean': 164.86, 'hr_std': 64.62, 'rmssd': 287.09, 'lf': 4848.08, 'hf': 6

[{'nni_mean': 362.31, 'hr_mean': 180.96, 'hr_std': 55.82, 'rmssd': 153.62, 'lf': 360.56, 'hf': 3524.14, 'LF/HF ratio': 0.1}, {'nni_mean': 354.26, 'hr_mean': 186.73, 'hr_std': 57.91, 'rmssd': 168.68, 'lf': 58.3, 'hf': 1477.26, 'LF/HF ratio': 0.04}, {'nni_mean': -17.19, 'hr_mean': 178.71, 'hr_std': 66.77, 'rmssd': 1974.95, 'lf': 51565.73, 'hf': 9915.6, 'LF/HF ratio': 5.2}, {'nni_mean': 365.0, 'hr_mean': 182.95, 'hr_std': 59.3, 'rmssd': 176.99, 'lf': 30.23, 'hf': 806.81, 'LF/HF ratio': 0.04}, {'nni_mean': 376.25, 'hr_mean': 175.2, 'hr_std': 54.76, 'rmssd': 179.22, 'lf': 274.08, 'hf': 4006.12, 'LF/HF ratio': 0.07}]
{'breath_avg_len': 3.33, 'inhale_duration': 5.7, 'avg_inhale': 1.9, 'exhale_duration': 4.28, 'avg_exhale': 2.14, 'inhale_exhale_ratio': 1.33}
[{'nni_mean': 354.26, 'hr_mean': 186.73, 'hr_std': 57.91, 'rmssd': 168.68, 'lf': 58.3, 'hf': 1477.26, 'LF/HF ratio': 0.04}, {'nni_mean': -17.19, 'hr_mean': 178.71, 'hr_std': 66.77, 'rmssd': 1974.95, 'lf': 51565.73, 'hf': 9915.6, 'LF/HF rat

Exception in thread Thread-1220323:
Traceback (most recent call last):
  File "/Users/annkatrin/opt/anaconda3/lib/python3.7/threading.py", line 926, in _bootstrap_inner
    self.run()
  File "/Users/annkatrin/opt/anaconda3/lib/python3.7/threading.py", line 1178, in run
    self.function(*self.args, **self.kwargs)
  File "/Users/annkatrin/Documents/Uni/Master/KTH/Master Project/biofeatures/notebooks/biofeatures.py", line 268, in update_loop
    self.update_timer.start()
  File "/Users/annkatrin/opt/anaconda3/lib/python3.7/threading.py", line 848, in start
    raise RuntimeError("threads can only be started once")
RuntimeError: threads can only be started once

Exception in thread Thread-1220339:
Traceback (most recent call last):
  File "/Users/annkatrin/opt/anaconda3/lib/python3.7/threading.py", line 926, in _bootstrap_inner
    self.run()
  File "/Users/annkatrin/opt/anaconda3/lib/python3.7/threading.py", line 1178, in run
    self.function(*self.args, **self.kwargs)
  File "/Users/an

## Launch on 2 devices

In [ ]:
from pythonosc import dispatcher, osc_server
from pythonosc.udp_client import SimpleUDPClient
import biofeatures
import time

# Use actuator IP
# Local Processing IP 192.168.0.100 or localhost 127.0.0.1, Arduino IP
actuator_ip = '127.0.0.1'
actuator_port = 32000
osc_client = SimpleUDPClient(actuator_ip, actuator_port) 


In [ ]:
val = 0.0
osc_client.send_message("/actuator/1/inflate", val)
osc_client.send_message("/actuator/2/inflate", val)


In [ ]:
val = 100.0
osc_client.send_message("/actuator/1/inflate", val)
osc_client.send_message("/actuator/2/inflate", val)


In [ ]:
deflate("1", 1)

In [ ]:
warmup_inflate("1", 3)

In [ ]:
warmup_inflate("2", 3)

In [ ]:
actuation_flag = True

pulsating("1", True)

In [ ]:
actuation_flag = False

In [ ]:
osc_client.send_message("/actuator/1/inflate", 0.0)

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline
plt.plot(np.linspace(0,len(resp_data)/200., len(resp_data) ), resp_data)

In [6]:
testvar = "Offset,3,3,3"

list(map(lambda x: int(x), testvar.split(",")[1:]))

[3, 3, 3]